In [2]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint
import pandas as pd

In [3]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [4]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'autosaurus', 'classDB', 'clevelandmuseum_art', 'config', 'local', 'petsitly_marketing', 'travel_db', 'uk_food']


In [5]:
# assign the uk_food database to a variable name
db = mongo['clevelandmuseum_art']
db

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'clevelandmuseum_art')

In [6]:
# review the collections in our new database
print(db.list_collection_names())

['artistsdata']


In [7]:
# review a document in the  collection
pprint(db.artistsdata.find_one())

{'_id': ObjectId('6676e22c41c62b1619c3155d'),
 'accession_number': '2020.113',
 'alternate_images': [],
 'artists_tags': ['male', 'Jewish artists'],
 'catalogue_raisonne': None,
 'citations': [{'citation': 'California Palace of the Legion of Honor. '
                            '<em>Catalogue, Inaugural Exposition of French Art '
                            'in the California Palace of the Legion of Honor, '
                            'Lincoln Park, San Francisco, California, '
                            '1924-1925</em>. San Francisco: Press of the James '
                            'H. Barry, 1924-1925.',
                'page_number': 'Mentioned: P. 20, no. 46; Reproduced: no. 46',
                'url': None},
               {'citation': 'Pissarro, Ludovico Rodo, and Lionello Venturi. '
                            '<em>Camille Pissarro; son art--son œuvre</em>. '
                            'Paris: P. Rosenberg, 1939.',
                'page_number': 'Mentioned: Vol. 1, p. 254, n

In [8]:
# assign the collection to a variable
artistsdata = db['artistsdata']
artistsdata

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'clevelandmuseum_art'), 'artistsdata')

In [9]:
# Count all documents in the collection
total_documents = artistsdata.count_documents({})
print(f"Total documents in the collection: {total_documents}")

Total documents in the collection: 47396


In [10]:
# Find how many documents have type as Painting
artistsdata.count_documents({'type': 'Painting'})

2503

Delete all the documents that is not required

In [11]:
#Delete all the documents that are not painting
#artistsdata.delete_many({'type': {'$ne': 'Painting'}})

In [12]:
# Check that other documents remain with 'find_one'
pprint(db.artistsdata.find_one())

{'_id': ObjectId('6676e22c41c62b1619c3155d'),
 'accession_number': '2020.113',
 'alternate_images': [],
 'artists_tags': ['male', 'Jewish artists'],
 'catalogue_raisonne': None,
 'citations': [{'citation': 'California Palace of the Legion of Honor. '
                            '<em>Catalogue, Inaugural Exposition of French Art '
                            'in the California Palace of the Legion of Honor, '
                            'Lincoln Park, San Francisco, California, '
                            '1924-1925</em>. San Francisco: Press of the James '
                            'H. Barry, 1924-1925.',
                'page_number': 'Mentioned: P. 20, no. 46; Reproduced: no. 46',
                'url': None},
               {'citation': 'Pissarro, Ludovico Rodo, and Lionello Venturi. '
                            '<em>Camille Pissarro; son art--son œuvre</em>. '
                            'Paris: P. Rosenberg, 1939.',
                'page_number': 'Mentioned: Vol. 1, p. 254, n

In [13]:
# Count all documents in the collection
total_documents = artistsdata.count_documents({})
print(f"Total documents in the collection: {total_documents}")

Total documents in the collection: 47396


In [14]:
# Define the aggregation pipeline stages
pipeline = [
    {
        '$addFields': {
            'artist_description': '$creators.description'
        }
    },
    {
        '$project': {
            '_id': 0,
            'artist_description': 1
        }
    }
]

result = list(artistsdata.aggregate(pipeline))

# Print the result
for doc in result:
    print(doc)

{'artist_description': ['Camille Pissarro (French, 1830–1903)']}
{'artist_description': ['Albert-Charles Lebourg (French, 1849–1928)']}
{'artist_description': ['Adolphe Yvon (French, 1817–1893)']}
{'artist_description': ['François Marius Granet (French, 1775–1849)']}
{'artist_description': ['Alfred Dehodencq (French, 1822–1882)']}
{'artist_description': ['Auguste Raffet (French, 1804–1860)']}
{'artist_description': ['Louis Rolland Trinquesse (French, c. 1746–c. 1800)']}
{'artist_description': ['Henri Joseph Harpignies (French, 1819–1916)']}
{'artist_description': ['Julien Léopold Boilly (French, 1796–1874)']}
{'artist_description': ['Mariano Fortuny (Spanish, 1838–1874)']}
{'artist_description': ['Henri Lehmann (French, 1814–1882)']}
{'artist_description': ['Henri Lehmann (French, 1814–1882)']}
{'artist_description': ['Isidore Pils (French, 1813/15–1875)']}
{'artist_description': ['Louis-Nicolas van Blarenberghe (French, 1716–1812)']}
{'artist_description': ['Jean Louis Forain (French,

In [15]:
#Delete all the documents that have creators field empty
#one time run
""" cursor = db.artistsdata.find({
    "creators": []
})

for document in cursor:
    pprint(document)

    db.artistsdata.delete_one({"_id": document["_id"]}) """

' cursor = db.artistsdata.find({\n    "creators": []\n})\n\nfor document in cursor:\n    pprint(document)\n\n    db.artistsdata.delete_one({"_id": document["_id"]}) '

Create the dataframe and apply the transformations on the data

In [16]:
# Fetch the data from the collection
data = list(artistsdata.find())
data

[{'_id': ObjectId('6676e22c41c62b1619c3155d'),
  'id': 74228,
  'accession_number': '2020.113',
  'share_license_status': 'CC0',
  'tombstone': 'Fishmarket, 1902. Camille Pissarro (French, 1830–1903). Oil on canvas; unframed: 66 x 81.3 cm (26 x 32 in.). The Cleveland Museum of Art, Nancy F. and Joseph P. Keithley Collection Gift 2020.113',
  'current_location': None,
  'title': 'Fishmarket',
  'title_in_original_language': None,
  'series': None,
  'series_in_original_language': None,
  'creation_date': '1902',
  'creation_date_earliest': 1902,
  'creation_date_latest': 1902,
  'artists_tags': ['male', 'Jewish artists'],
  'culture': ['France, 20th century'],
  'technique': 'oil on canvas',
  'support_materials': [],
  'department': 'Modern European Painting and Sculpture',
  'collection': 'Mod Euro - Painting 1800-1960',
  'type': 'Painting',
  'measurements': 'Unframed: 66 x 81.3 cm (26 x 32 in.)',
  'dimensions': {'unframed': {'height': 0.66, 'width': 0.813},
   'framed': {'height':

In [17]:
paintings_df = pd.DataFrame(data)
paintings_df.head()


_id     id accession_number share_license_status  \
0  6676e22c41c62b1619c3155d  74228         2020.113                  CC0   
1  6676e22c41c62b1619c3155e  74539         2015.449                  CC0   
2  6676e22c41c62b1619c3155f  74540         2015.451                  CC0   
3  6676e22c41c62b1619c31560  74551        2018.1059                  CC0   
4  6676e22c41c62b1619c31561  74553        2018.1060                  CC0   

                                           tombstone current_location  \
0  Fishmarket, 1902. Camille Pissarro (French, 18...             None   
1  A Miller's Carriage, c. 1895. Albert-Charles L...             None   
2  Leda and the Swan, c. 1846–83. Adolphe Yvon (F...             None   
3  The Monks, c. 1802–30. François Marius Granet ...             None   
4  Study Sheet, c. 1870–80. Alfred Dehodencq (Fre...             None   

                 title title_in_original_language series  \
0           Fishmarket                       None   None   
1  A Miller's Carriage                       None   None   
2    Leda and the Swan                       None   None   
3            The Monks                       None   None   
4          Study Sheet                       None   None   

  series_in_original_language  ... catalogue_raisonne  \
0                        None  ...               None   
1                        None  ...               None   
2                        None  ...               None   
3                        None  ...               None   
4                        None  ...               None   

                                      url  \
0   https://clevelandart.org/art/2020.113   
1   https://clevelandart.org/art/2015.449   
2   https://clevelandart.org/art/2015.451   
3  https://clevelandart.org/art/2018.1059   
4  https://clevelandart.org/art/2018.1060   

                                              images alternate_images  \
0  {'annotation': None, 'web': {'url': 'https://o...               []   
1  {'annotation': None, 'web': {'url': 'https://o...               []   
2  {'annotation': None, 'web': {'url': 'https://o...               []   
3  {'annotation': None, 'web': {'url': 'https://o...               []   
4  {'annotation': None, 'web': {'url': 'https://o...               []   

                                        creditline sketchfab_id sketchfab_url  \
0  Nancy F. and Joseph P. Keithley Collection Gift         None          None   
1                         Bequest of Muriel Butkin         None          None   
2                         Bequest of Muriel Butkin         None          None   
3                         Bequest of Muriel Butkin         None          None   
4                         Bequest of Muriel Butkin         None          None   

  gallery_donor_text                                           creators  \
0               None  [{'id': 1836, 'description': 'Camille Pissarro...   
1               None  [{'id': 53727, 'description': 'Albert-Charles ...   
2               None  [{'id': 53730, 'description': 'Adolphe Yvon (F...   
3               None  [{'id': 1703, 'description': 'François Marius ...   
4               None  [{'id': 53773, 'description': 'Alfred Dehodenc...   

                   updated_at  
0  2024-05-14 11:07:12.474000  
1  2024-05-17 11:33:13.672000  
2  2024-05-17 11:33:13.678000  
3  2024-05-17 11:33:13.684000  
4  2024-05-17 11:33:13.690000  

[5 rows x 45 columns]

In [18]:
column_names = paintings_df.columns
column_names

Index(['_id', 'id', 'accession_number', 'share_license_status', 'tombstone',
       'current_location', 'title', 'title_in_original_language', 'series',
       'series_in_original_language', 'creation_date',
       'creation_date_earliest', 'creation_date_latest', 'artists_tags',
       'culture', 'technique', 'support_materials', 'department', 'collection',
       'type', 'measurements', 'dimensions', 'state_of_the_work',
       'edition_of_the_work', 'copyright', 'inscriptions', 'exhibitions',
       'provenance', 'find_spot', 'related_works', 'former_accession_numbers',
       'did_you_know', 'description', 'external_resources', 'citations',
       'catalogue_raisonne', 'url', 'images', 'alternate_images', 'creditline',
       'sketchfab_id', 'sketchfab_url', 'gallery_donor_text', 'creators',
       'updated_at'],
      dtype='object')

In [19]:
required_df = paintings_df[['id', 'accession_number', 'tombstone', 'title', 'creation_date', 'technique','department','collection','type', 'creators']]
required_df

id accession_number  \
0       74228         2020.113   
1       74539         2015.449   
2       74540         2015.451   
3       74551        2018.1059   
4       74553        2018.1060   
...       ...              ...   
47391  540567          2024.20   
47392  540568          2024.21   
47393  617630          2024.25   
47394  670789          2024.24   
47395  670914          2024.26   

                                               tombstone  \
0      Fishmarket, 1902. Camille Pissarro (French, 18...   
1      A Miller's Carriage, c. 1895. Albert-Charles L...   
2      Leda and the Swan, c. 1846–83. Adolphe Yvon (F...   
3      The Monks, c. 1802–30. François Marius Granet ...   
4      Study Sheet, c. 1870–80. Alfred Dehodencq (Fre...   
...                                                  ...   
47391  Snowy Night, Woodstock, Vermont, 1940, printed...   
47392  Iowa: House with Melting Roof, Pomeroy, Ohio, ...   
47393  Dreaming in English (shadow dance), 2021. Nich...   
47394  Sleeping by the River, Tecun-Uman Guatemala, 2...   
47395  Montaña Roja–Funeral, c. 2003–23. César Rodrig...   

                                             title          creation_date  \
0                                       Fishmarket                   1902   
1                              A Miller's Carriage                c. 1895   
2                                Leda and the Swan             c. 1846–83   
3                                        The Monks             c. 1802–30   
4                                      Study Sheet             c. 1870–80   
...                                            ...                    ...   
47391              Snowy Night, Woodstock, Vermont  1940, printed c. 1975   
47392       House with Melting Roof, Pomeroy, Ohio                   1971   
47393           Dreaming in English (shadow dance)                   2021   
47394  Sleeping by the River, Tecun-Uman Guatemala                   2020   
47395                         Montaña Roja–Funeral             c. 2003–23   

                                               technique  \
0                                          oil on canvas   
1      black and white chalk with stumping on beige w...   
2           Charcoal and gouache with touches of pastel    
3            watercolor, pen and brown ink on laid paper   
4      pen and dark brown ink, watercolor with graphi...   
...                                                  ...   
47391                               gelatin silver print   
47392                               gelatin silver print   
47393                    Monotype and gold leaf on paper   
47394                                      digital print   
47395                                       inkjet print   

                                   department                     collection  \
0      Modern European Painting and Sculpture  Mod Euro - Painting 1800-1960   
1                                    Drawings                    DR - French   
2                                    Drawings                    DR - French   
3                                    Drawings                    DR - French   
4                                    Drawings                    DR - French   
...                                       ...                            ...   
47391                             Photography        PH - American 1900-1950   
47392                             Photography     PH - American 1951-Present   
47393                                  Prints                  PR - Monotype   
47394                             Photography     PH - American 1951-Present   
47395                             Photography                   PH - Mexican   

             type                                           creators  
0        Painting  [{'id': 1836, 'description': 'Camille Pissarro...  
1         Drawing  [{'id': 53727, 'description': 'Albert-Charles ...  
2         Drawing  [{'id': 53730, 'description': 'Adolphe Yvo

In [20]:
#tombstone="A Miller's Carriage, c. Albert-Charles L ( ram)"
#tombstone="A Miller's Carriage,() c. Albert-Charles L ( ram)"
#tombstone="Dreaming in English (shadow dance), 2021. Nicho"
tombstone ="Fishmarket, 1902. Camille Pissarro (French, 1830â€“1903). Oil on canvas; unframed: 66 x 81.3 cm (26 x 32 in.). The Cleveland Museum of Art, Nancy F. and Joseph P. Keithley Collection Gift 2020.113"
#tombstone="A Miller's Carriage, c. 1895. Albert-Charles Lebourg (French, 1849–192…"
#tombstone="Fishmarket, 1902. Camille Pissarro (French, 1830–1903). Oil on canvas;…"
#artist_info = tombstone.split(".",1)[1].split(".")[0].strip().split("(")[0].strip()
artist_info = tombstone.split("(")[0].split(".")[-1].strip()
#artist_info = tombstone.split(".",1)[1].split(".")[-1].strip().split("(")[0].strip()
#split("(")[0].split(".")[-1].strip()
#.combine_first(tombstone)
#.split("(")[0].strip()
artist_info

'Camille Pissarro'

In [21]:
""" def extract_author_name(creators, description):
    if description in creators:

        #artist_info = tombstone.split(".")[1].strip()
        #artist_info = tombstone.rsplit(".",1)[1].strip()
        #artist_name = artist_info.split("(")[0].strip()
        #artist_name = tombstone.split("(")[0].split(".")[-1].strip()
        #artist_name = tombstone.split(".",1)[1].split(".")[-1].strip().split("(")[0].strip()
       
        #split(".",1)[1].split(".")[-1].strip().split("(")[0].strip()
        return artist_name
    else:
        return None
    
    # Apply the function to create a new column with author names
#required_df['authorname'] = required_df['creators'].apply(extract_author_name())
required_df['authorname'] = required_df['creators'].apply(lambda x:extract_author_name(x, 'descrption'))
required_df """


def extract_author_name(tombstone):
    if tombstone:
        artist_name = tombstone.split("(")[0].split(".")[-1].strip()
        return artist_name
    else:
        return None
    
    # Apply the function to create a new column with author names
required_df['authorname'] = required_df['tombstone'].apply(extract_author_name)
required_df

C:\Users\sarit\AppData\Local\Temp\ipykernel_31908\735137322.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  required_df['authorname'] = required_df['tombstone'].apply(extract_author_name)


id accession_number  \
0       74228         2020.113   
1       74539         2015.449   
2       74540         2015.451   
3       74551        2018.1059   
4       74553        2018.1060   
...       ...              ...   
47391  540567          2024.20   
47392  540568          2024.21   
47393  617630          2024.25   
47394  670789          2024.24   
47395  670914          2024.26   

                                               tombstone  \
0      Fishmarket, 1902. Camille Pissarro (French, 18...   
1      A Miller's Carriage, c. 1895. Albert-Charles L...   
2      Leda and the Swan, c. 1846–83. Adolphe Yvon (F...   
3      The Monks, c. 1802–30. François Marius Granet ...   
4      Study Sheet, c. 1870–80. Alfred Dehodencq (Fre...   
...                                                  ...   
47391  Snowy Night, Woodstock, Vermont, 1940, printed...   
47392  Iowa: House with Melting Roof, Pomeroy, Ohio, ...   
47393  Dreaming in English (shadow dance), 2021. Nich...   
47394  Sleeping by the River, Tecun-Uman Guatemala, 2...   
47395  Montaña Roja–Funeral, c. 2003–23. César Rodrig...   

                                             title          creation_date  \
0                                       Fishmarket                   1902   
1                              A Miller's Carriage                c. 1895   
2                                Leda and the Swan             c. 1846–83   
3                                        The Monks             c. 1802–30   
4                                      Study Sheet             c. 1870–80   
...                                            ...                    ...   
47391              Snowy Night, Woodstock, Vermont  1940, printed c. 1975   
47392       House with Melting Roof, Pomeroy, Ohio                   1971   
47393           Dreaming in English (shadow dance)                   2021   
47394  Sleeping by the River, Tecun-Uman Guatemala                   2020   
47395                         Montaña Roja–Funeral             c. 2003–23   

                                               technique  \
0                                          oil on canvas   
1      black and white chalk with stumping on beige w...   
2           Charcoal and gouache with touches of pastel    
3            watercolor, pen and brown ink on laid paper   
4      pen and dark brown ink, watercolor with graphi...   
...                                                  ...   
47391                               gelatin silver print   
47392                               gelatin silver print   
47393                    Monotype and gold leaf on paper   
47394                                      digital print   
47395                                       inkjet print   

                                   department                     collection  \
0      Modern European Painting and Sculpture  Mod Euro - Painting 1800-1960   
1                                    Drawings                    DR - French   
2                                    Drawings                    DR - French   
3                                    Drawings                    DR - French   
4                                    Drawings                    DR - French   
...                                       ...                            ...   
47391                             Photography        PH - American 1900-1950   
47392                             Photography     PH - American 1951-Present   
47393                                  Prints                  PR - Monotype   
47394                             Photography     PH - American 1951-Present   
47395                             Photography                   PH - Mexican   

             type                                           creators  \
0        Painting  [{'id': 1836, 'description': 'Camille Pissarro...   
1         Drawing  [{'id': 53727, 'description': 'Albert-Charles ...   
2         Drawing  [{'id': 53730, 'description': 'Adolphe 

Creating the data frame for 101 artists and filter the records

In [22]:
artists101_csv= r"C:\Users\sarit\OneDrive\Desktop\Class_Folder\mygithub\project-3\101.csv"

In [23]:
artists101_df = pd.read_csv(artists101_csv)
artists101_df

nameP colloq_name   last_name    lifespanP  \
0                    Pablo Picasso      Picasso     Picasso    1881-1973   
1                Giotto Di Bondone       Giotto  Di Bondone  c.1267-1337   
2                Leonardo Da Vinci     Leonardo    Da Vinci    1452-1519   
3                     Paul Cézanne      Cézanne     Cézanne    1839-1906   
4               Rembrandt Van Rijn    Rembrandt        Rijn    1606-1669   
..                              ...         ...         ...          ...   
96      William-Adolphe Bouguereau   Bouguereau  Bouguereau    1825-1905   
97                  Gustave Moreau       Moreau      Moreau    1826-1898   
98              Giorgio De Chirico   De Chirico  De Chirico    1888-1978   
99                   Fernand Léger        Léger       Léger    1881-1955   
100  Jean-Auguste-Dominique Ingres       IngrEs      Ingres    1780-1867   

     separator                                                bio  
0            1  Love him or hate him, Pablo Picasso changed it...  
1            1  The greatest renovator of early European paint...  
2            1  There is no artist more legendary than Leonard...  
3            1  “Cézanne is the father of us all”. This lapida...  
4            2  The fascinating, magnetic interplay of light a...  
..         ...                                                ...  
96           1  Another case of “love him or hate him” artist....  
97           1  One of the key figures of symbolism, introvert...  
98           1  Considered the father of metaphysical painting...  
99           1  A pure cubist painter during his early decades...  
100          1  Ingres was the most prominent disciple of the ...  

[101 rows x 6 columns]

In [24]:
#merged_df = pd.merge(required_df, artists101_df, left_on='authorname', right_on='nameP', how='left')
required_df['authorname']=required_df['authorname'].str.strip()
artists101_df['nameP']=artists101_df['nameP'].str.strip()
merged_df = pd.merge(required_df, artists101_df, left_on='authorname',right_on='nameP')
merged_df


C:\Users\sarit\AppData\Local\Temp\ipykernel_31908\638616375.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  required_df['authorname']=required_df['authorname'].str.strip()


id accession_number  \
0      74601         2021.108   
1      95259        1916.1032   
2     107952         1925.578   
3     110384           1929.1   
4     113856         1933.145   
...      ...              ...   
1535  166228     2008.157.2.m   
1536  159272          1995.68   
1537  164618         2006.133   
1538  160715          1998.74   
1539  292525         2016.304   

                                              tombstone  \
0     Two Boats at the Harbor of Dieppe, 1854. Eugèn...   
1     Greek Cavalry Men Resting in Forest, 1858. Eug...   
2     A Trapped Tiger, 1854. Eugène Delacroix (Frenc...   
3     The Blacksmith, 1833. Eugène Delacroix (French...   
4     Illustrations for Faust, 1828. Eugène Delacroi...   
...                                                 ...   
1535  SMS: A Collection of Multiples, vol. 2: Contre...   
1536  The Woman with the Spider Web between Bare Tre...   
1537  Footbridge with Cross before Trees at a River,...   
1538  Elizabeth II, 1966. Gerhard Richter (German, 1...   
1539  Reclining Female Nude. William-Adolphe Bouguer...   

                                                 title creation_date  \
0                    Two Boats at the Harbor of Dieppe          1854   
1                  Greek Cavalry Men Resting in Forest          1858   
2                                      A Trapped Tiger          1854   
3                                       The Blacksmith          1833   
4                              Illustrations for Faust          1828   
...                                                ...           ...   
1535                                     Contrepèterie          1968   
1536  The Woman with the Spider Web between Bare Trees          1803   
1537     Footbridge with Cross before Trees at a River        c.1803   
1538                                      Elizabeth II          1966   
1539                             Reclining Female Nude          None   

                                              technique  \
0     watercolor and pencil on paper laid down on board   
1                                         oil on fabric   
2                                          cliché-verre   
3                                              aquatint   
4                                            lithograph   
...                                                 ...   
1535  Seven minute recording of surrealist word game...   
1536                                            woodcut   
1537                                            etching   
1538                            color offset lithograph   
1539                    Graphite, heightened with white   

                                  department                     collection  \
0                                   Drawings                    DR - French   
1     Modern European Painting and Sculpture  Mod Euro - Painting 1800-1960   
2                                     Prints              PR - Cliché verre   
3                                     Prints                  PR - Aquatint   
4                                     Prints                PR - Lithograph   
...                                      ...                            ...   
1535                                  Prints                         Prints   
1536                                  Prints                   PR - Woodcut   
1537                                  Prints                   PR - Etching   
1538                                  Prints                PR - Lithograph   
1539                                Drawings                    DR - French   

             type                                           creators  \
0         Drawing  [{'id': 1658, 'description': 'Eugène Delacroix...   
1        Painting  [{'id': 1658, 'description': 'Eugène Delacroix...   
2           Print  [{'id': 1658, 'description': 'Eugène Delacroix...   
3           Print  [{'id': 1658, 'description': 'Eugène Delacroix...   
4           Print  [{

In [25]:
# Count the number of classifications
unique_counts = merged_df['type'].value_counts()
print(unique_counts)

type
Print                 1153
Mixed Media             99
Drawing                 89
Painting                73
Bound Volume            66
Portfolio               37
Photograph              17
Sculpture                3
Plate                    2
Lithographic Stone       1
Name: count, dtype: int64


In [44]:
clevelandmoa_df = merged_df[[ 'nameP','colloq_name', 'title', 'creation_date', 'department','type']]
clevelandmoa_df

nameP colloq_name  \
0               Eugène Delacroix   Delacroix   
1               Eugène Delacroix   Delacroix   
2               Eugène Delacroix   Delacroix   
3               Eugène Delacroix   Delacroix   
4               Eugène Delacroix   Delacroix   
...                          ...         ...   
1535              Marcel Duchamp     Duchamp   
1536      Caspar David Friedrich   Friedrich   
1537      Caspar David Friedrich   Friedrich   
1538             Gerhard Richter     Richter   
1539  William-Adolphe Bouguereau  Bouguereau   

                                                 title creation_date  \
0                    Two Boats at the Harbor of Dieppe          1854   
1                  Greek Cavalry Men Resting in Forest          1858   
2                                      A Trapped Tiger          1854   
3                                       The Blacksmith          1833   
4                              Illustrations for Faust          1828   
...                                                ...           ...   
1535                                     Contrepèterie          1968   
1536  The Woman with the Spider Web between Bare Trees          1803   
1537     Footbridge with Cross before Trees at a River        c.1803   
1538                                      Elizabeth II          1966   
1539                             Reclining Female Nude          None   

                                  department         type  
0                                   Drawings      Drawing  
1     Modern European Painting and Sculpture     Painting  
2                                     Prints        Print  
3                                     Prints        Print  
4                                     Prints        Print  
...                                      ...          ...  
1535                                  Prints  Mixed Media  
1536                                  Prints        Print  
1537                                  Prints        Print  
1538                                  Prints        Print  
1539                                Drawings      Drawing  

[1540 rows x 6 columns]

In [46]:
# Renamimg the field names
clevelandmoa_df=clevelandmoa_df.rename(columns={'nameP': 'fullname'})
clevelandmoa_df

fullname colloq_name  \
0               Eugène Delacroix   Delacroix   
1               Eugène Delacroix   Delacroix   
2               Eugène Delacroix   Delacroix   
3               Eugène Delacroix   Delacroix   
4               Eugène Delacroix   Delacroix   
...                          ...         ...   
1535              Marcel Duchamp     Duchamp   
1536      Caspar David Friedrich   Friedrich   
1537      Caspar David Friedrich   Friedrich   
1538             Gerhard Richter     Richter   
1539  William-Adolphe Bouguereau  Bouguereau   

                                                 title creation_date  \
0                    Two Boats at the Harbor of Dieppe          1854   
1                  Greek Cavalry Men Resting in Forest          1858   
2                                      A Trapped Tiger          1854   
3                                       The Blacksmith          1833   
4                              Illustrations for Faust          1828   
...                                                ...           ...   
1535                                     Contrepèterie          1968   
1536  The Woman with the Spider Web between Bare Trees          1803   
1537     Footbridge with Cross before Trees at a River        c.1803   
1538                                      Elizabeth II          1966   
1539                             Reclining Female Nude          None   

                                  department         type  
0                                   Drawings      Drawing  
1     Modern European Painting and Sculpture     Painting  
2                                     Prints        Print  
3                                     Prints        Print  
4                                     Prints        Print  
...                                      ...          ...  
1535                                  Prints  Mixed Media  
1536                                  Prints        Print  
1537                                  Prints        Print  
1538                                  Prints        Print  
1539                                Drawings      Drawing  

[1540 rows x 6 columns]

In [47]:
clevelandmoa_df.to_csv('clevelandmoa.csv', index=False)